In [185]:
# imports
import json, re, time, unicodedata, unidecode, codecs
from lxml import etree
from pattern.nl import parse, split, parsetree
from collections import defaultdict, Counter
from datetime import date, datetime, timedelta

In [5]:
# files
#MWE
#topics = json.load(open('D:\\4. Data\\Amazones_Forum_Export_JSON\\MWE_topic.json'))
#posts = json.load(open('D:\\4. Data\\Amazones_Forum_Export_JSON\\MWE.json'))
#regular
forums = json.load(open('D:\\4. Data\\Amazones_Forum_Export_JSON\\2017-12-07T13-35-45 _amazones_forums_export.json'))
topics = json.load(open('D:\\4. Data\\Amazones_Forum_Export_JSON\\2017-12-07T13-36-51_amazones_forum_topics_export.json'))
posts = json.load(open('D:\\4. Data\\Amazones_Forum_Export_JSON\\2017-12-07T13-39-20_amazones_forum_posts_export.json'))
users = json.load(open('D:\\4. Data\\Amazones_Forum_Export_JSON\\2017-12-07T13-39-20_amazones_users_export.json'))

In [90]:
count = 1
for post in topics:
    print post
    count -=1
    if count<=0:
        break

{u'Body': u'<p>\n</p><p>Even een hele praktische vraag: weet iemand of je na een bloedtransfusie zelf naar huis mag/kunt rijden?</p>\n\n', u'Path': u'/en/node/22217', u'Title': u'bloedtransfusie en autorijden', u'Updated date': u'03/12/2017 - 10:52', u'Nid': u'22217', u'Post date': u'03/12/2017 - 10:50', u'Author uid': u'4602', u'Forums': u'221'}


In [177]:
# make two dictionaries: user's post T imes, and user's P ost texts.
count = 200
P = defaultdict(list)
T = defaultdict(list)
datetimelist = []

for t in reversed(topics):
    P[t['Author uid']].append(t['Body'])
    T[t['Author uid']].append(t['Post date'])
    datetimelist.append(datetime.strptime(t['Post date'], '%d/%m/%Y - %H:%M'))
    
    count-=1
    if count-1<=0:
        break
    for p in reversed(posts):
        if p['Forum Topic ID'] == t['Nid']:
            P[p['Auteur-uid']].append(p['Body'])
            T[p['Auteur-uid']].append(p['Datum van inzending'])
            datetimelist.append(datetime.strptime(p['Datum van inzending'], '%d/%m/%Y - %H:%M'))

            count-=1
            if count-1<=0:
                break

In [182]:
def binlist(datetimelist):
    lower = min(datetimelist)
    upper = max(datetimelist)

    if lower.time()>=datetime.strptime('4:00','%H:%M').time():
        lower = lower.replace(hour = 4, minute = 0)
    else:
        lower = (lower+timedelta(days = -1)).replace(hour=4,minute=0)

    if upper.time()<datetime.strptime('12:00','%H:%M').time():
        upper = upper.replace(hour = 4, minute = 0)
    else:
        upper = (upper+timedelta(days=1)).replace(hour=4,minute=0)

    return([lower + timedelta(days=x) for x in range(0, (upper-lower).days)])

In [183]:
bindict = defaultdict(list)
postdict = defaultdict(list)
binlist = binlist(datetimelist)

for user in T:
    for index,boundary in enumerate(binlist):
        if index+1>=len(binlist):
            break
        else:
            lower = binlist[index]
            upper = binlist[index+1]

            for time in T[user]:
                post = P[user][T[user].index(time)]
                if lower<=datetime.strptime(time, '%d/%m/%Y - %H:%M')<upper:
                    bindict[lower,upper].append(time)
                    postdict[lower,upper].append(post)
                    # sentiment
                    # objectivity
                    # nr of question marks
                    # length of post (in words, sentences or characters... or something)
                    
                    # fill up empty places in dictionary: if len(dict[x]==0: dict[x]=[])
                    
    #print user
    #pprint(bindict.items())
    pprint(postdict.items())

[((datetime.datetime(2007, 1, 20, 4, 0),
   datetime.datetime(2007, 1, 21, 4, 0)),
  [u'<p>\n</p><div class="bb-quote"><b>twin schreef:</b><br /><blockquote class="bb-quote-body">Ik heb het over botontkalking met mijn huisarts gehad en hij zei dat ik wat extra melk producten moets nemen.<br />\nDat ik daar verder niets voor hoefde nemen.<br />\nEn dat hij over een poosje een botdichtheidsmeting ging regelen...</blockquote>\n</div>\n\n<p>Ik heb me suf zitten peinzen waar ik de artikelen (oa van de WHO) kon vinden, niet gelukt (sorry)  :oops: , maar toch maar even zeggen (zonder verwijzingen en links dan nog): uit onderzoek blijkt dat de calcium in melk(producten) de calcium is die het slechtst opgenomen wordt in het lichaam... Het feit dat je melk(producten) moet drinken om botontkalking te voorkomen is achterhaald en het verbaast me dat een arts dat nog adviseert. In bv de Verenigde Staten, waar de meeste zuivel geconsumeerd wordt per hoofd van de bevolking is ook het aantal mensen dat

[((datetime.datetime(2006, 3, 13, 4, 0),
   datetime.datetime(2006, 3, 14, 4, 0)),
  [u"<p>Ha Goudblok, ik word maandag de 20e opgenomen en de verwachting is dat ik dan 1 of 2 nachtjes moet blijven. Morgen (de 14e) ben ik 's middags is het AVL: bloedprikken, mondhygienist, kweekjes van de keel afnemen etc....</p>\n"]),
 ((datetime.datetime(2006, 4, 5, 4, 0), datetime.datetime(2006, 4, 6, 4, 0)),
  [u"<p>We zijn inmiddels weer een paar weken verder en de eerste etappe van de mini CTC is genomen: bijna drie weken geleden heb ik de chemo's gekregen en een paar dagen later de terugplaatsing van de (mijn eigen) stamcellen. </p>\n<p>Het was de de week van de 20e een bijzondere week voor de verpleging op 4B (en eigenlijk ook voor de betrokken artsen); in de ene kamer lag een mevrouw die de laatste 'klassieke' CTC (hoge dosis chemo) van het AVL kreeg (in 1x een chemo die ongeveer 10 keer hoger gedoseerd is dan een 'normale', waarbij de patient ongeveer twee/drie weken opgenomen moet worden in 

[((datetime.datetime(2006, 3, 13, 4, 0),
   datetime.datetime(2006, 3, 14, 4, 0)),
  [u"<p>Ha Goudblok, ik word maandag de 20e opgenomen en de verwachting is dat ik dan 1 of 2 nachtjes moet blijven. Morgen (de 14e) ben ik 's middags is het AVL: bloedprikken, mondhygienist, kweekjes van de keel afnemen etc....</p>\n"]),
 ((datetime.datetime(2006, 4, 5, 4, 0), datetime.datetime(2006, 4, 6, 4, 0)),
  [u"<p>We zijn inmiddels weer een paar weken verder en de eerste etappe van de mini CTC is genomen: bijna drie weken geleden heb ik de chemo's gekregen en een paar dagen later de terugplaatsing van de (mijn eigen) stamcellen. </p>\n<p>Het was de de week van de 20e een bijzondere week voor de verpleging op 4B (en eigenlijk ook voor de betrokken artsen); in de ene kamer lag een mevrouw die de laatste 'klassieke' CTC (hoge dosis chemo) van het AVL kreeg (in 1x een chemo die ongeveer 10 keer hoger gedoseerd is dan een 'normale', waarbij de patient ongeveer twee/drie weken opgenomen moet worden in 

[((datetime.datetime(2006, 3, 13, 4, 0),
   datetime.datetime(2006, 3, 14, 4, 0)),
  [u"<p>Ha Goudblok, ik word maandag de 20e opgenomen en de verwachting is dat ik dan 1 of 2 nachtjes moet blijven. Morgen (de 14e) ben ik 's middags is het AVL: bloedprikken, mondhygienist, kweekjes van de keel afnemen etc....</p>\n"]),
 ((datetime.datetime(2006, 4, 5, 4, 0), datetime.datetime(2006, 4, 6, 4, 0)),
  [u"<p>We zijn inmiddels weer een paar weken verder en de eerste etappe van de mini CTC is genomen: bijna drie weken geleden heb ik de chemo's gekregen en een paar dagen later de terugplaatsing van de (mijn eigen) stamcellen. </p>\n<p>Het was de de week van de 20e een bijzondere week voor de verpleging op 4B (en eigenlijk ook voor de betrokken artsen); in de ene kamer lag een mevrouw die de laatste 'klassieke' CTC (hoge dosis chemo) van het AVL kreeg (in 1x een chemo die ongeveer 10 keer hoger gedoseerd is dan een 'normale', waarbij de patient ongeveer twee/drie weken opgenomen moet worden in 

 ((datetime.datetime(2011, 5, 3, 4, 0), datetime.datetime(2011, 5, 4, 4, 0)),
  [u'<p>Scarlett, lastige keuze. Wat je mogelijk zou willen weten in zo\'n geval is: wordt het volledig vergoed? hoeveel vertraging loop je op met de start van de chemo? welk percentage van de eicellen overleeft het bevriezen &amp; ontdooien en zou dus in de toekomst nog \'bruikbaar\' zijn? hoe groot is de kans dat je onvruchtbaar wordt door de chemo? Dan kun je een afweging maken of het voor jou van toegevoegde waarde is.</p>\n<p>Overigens zijn er ook wel vrouwen die voorafgaand aan de chemo hun eierstokken tijdelijk plat laten leggen. De theorie is dat die dan minder schade oplopen door de chemo. Daar gebruiken ze dan dezelfde injecties voor als de hormoongevoeligen krijgen als onderdeel van hormoontherapie. Lees  :arrow:  <a href="http://de-amazones.nl/phpbbforum/viewtopic.php?f=46&amp;t=5058" class="bb-url" rel="nofollow">hier</a> maar. Het is enkel theorie, bewijs is er (nog?) niet voor, maar je raakt wa

...

 ((datetime.datetime(2005, 9, 29, 4, 0),
   datetime.datetime(2005, 9, 30, 4, 0)),
  [u"<p>Ik heb ook sinds een paar maanden last van mijn rug (erg stijf gevoel) en inderdaad ook soms mijn heupen. Ben dus maar weer eens gaan lezen op het forum en ontdek dat jullie hier dus ook erg veel last van hebben. Met name veel zitten (wat ik dus op mijn werk doe) en met omdraaien in bed. Ben ook wel weer opgelucht dat ik lees dat jullie hier last van hebben, want soms maak je je toch wel een beetje zorgen erover. Dan denk je of zou ik toch uitzaaiingen hebben en een volgend moment denk je dan weer, stel je niet aan, 't zijn gewoon je spieren.</p>\n"]),
 ((datetime.datetime(2007, 1, 29, 4, 0),
   datetime.datetime(2007, 1, 30, 4, 0)),
  [u'<p><span style="color:indigo">omhoog voor ervaringen met het invriezen van eicellen</span></p>\n']),
 ((datetime.datetime(2005, 5, 18, 4, 0),
   datetime.datetime(2005, 5, 19, 4, 0)),
  [u"<p>Hoi Jori,</p>\n<p>Ik gebruik zoladex en arimidex, en heb ook last van 

  [u"<p>Hoi Jori,</p>\n<p>Ik gebruik zoladex en arimidex, en heb ook last van gewrichtspijn. Het begon met tintelende handen, vooral als ik wakker werd. Nu heb ik er vaak last van dat mijn vingers 'op slot' gaan als ik ze gebogen heb, vooral als ik ze ver buig. Ik heb ook een tijdje mijn duim juist niet kunnen buigen, maar dat ging weer over. Ik denk dat licht sporten wel helpt omdat het de boel soepeler maakt, maar van oefeningen waar ik veel kracht moet gebruiken krijg ik juist last. Ik dacht eerst dat temperatuur ook een rol speelde, maar dat blijkt toch weinig uit te maken. Gelukkig maar, want anders zit je met het dilemma: warm met opvliegers of koud met gewrichtsklachten. Volgens mijn onco komt het van de overgang. </p>\n<p>groetjes</p>\n",
   u'<p>Hoi,</p>\n<p>Ik gebruik Arimidex en heb mijn eierstokken laten verwijderen. Na het verwijderen heb ik veel last van mijn schoudergewricht (niet geopereerde kant), kniegewricht en rug. Ik ben ook ontzettend stijf geworden, na 5 minuten 

   datetime.datetime(2005, 10, 27, 4, 0)),
  [u'<p>hoi bambie </p>\n<p>ik ben ook onder behandeling geweest in voorburg en heb ook mijn eicellen in laten vriezen als je iets wilt weten mail dan of msn?</p>\n<p>liefs jertam</p>\n',
   u'<p>foutje verkeerd gelezen </p>\n<p>maar sophia als je wat wilt weten vraag maar</p>\n<p>SORRY nogmaals :oops:</p>\n',
   u'<p><span style="color:indigo">Het is Sophia niet Bambie (of Bambi) die bezig is info te verzamelen over dit onderwerp.</span></p>\n']),
 ((datetime.datetime(2007, 3, 15, 4, 0),
   datetime.datetime(2007, 3, 16, 4, 0)),
  [u"<p>oh jee, <br />\nik was vandaag bij de chirurg en vroeg of het heel erg zou zijn om te stoppen mat de tamoxifen, omdat ik zulke stijve gewrichten heb, niet meer normaal, ik kan niet meer mijn werk doen s\xf3chtends en stuit daar op veel onbegrip,<br />\nmaar volgens hem was het risico erg groot,<br />\nhet is zo erg dat mijn armen s'ochtends regelmatig iets uit de kom gaan, ik heb veel fysio gehad, maar dat hel

   datetime.datetime(2005, 11, 2, 4, 0)),
  [u"<p>ook ik gebruik zoladex 1 keer per maand en ook tamoxifen.<br />\nwat een opluchtig jullie verhalen!!!!!!!!!!!was al zo bang.kan al ruim een week niet normaal meer lopen.last van me benen,heupen,rug,schouders en sleutelbeen.pffff kan niet normaal zitten,liggen of lopen van de pyn.wat was ik bang zeg,want de vertrouwe in je lichaam was ik al beetje kwyt.nou moet ik 17 nov een botscan doen,dus hopen dat ut van de pillen komt.moet zeggen dat opvliegers mee vallen,heb ze wel.als ik net prik gehad :twisted: heb dan ben ik echt week bha!!!!!!!!!!s'nachts misselyk,niet echt aardig,hihi.hoop wel dat pyn minder wordt :twisted: want dit is echt niet leuk meer,voel me echt shit,en idd een oud wyf in een lichaam van 33jaar!!!!!!!!!!!!!!</p>\n"]),
 ((datetime.datetime(2011, 5, 5, 4, 0), datetime.datetime(2011, 5, 6, 4, 0)),
  [u'<p>Ik hoop niet dat ik nog een rekening nagestuurd krijg. Zou lekker zijn. Heb het vorig jaar september gedaan. Dus van het

   datetime.datetime(2005, 9, 30, 4, 0)),
  [u"<p>Ik heb ook sinds een paar maanden last van mijn rug (erg stijf gevoel) en inderdaad ook soms mijn heupen. Ben dus maar weer eens gaan lezen op het forum en ontdek dat jullie hier dus ook erg veel last van hebben. Met name veel zitten (wat ik dus op mijn werk doe) en met omdraaien in bed. Ben ook wel weer opgelucht dat ik lees dat jullie hier last van hebben, want soms maak je je toch wel een beetje zorgen erover. Dan denk je of zou ik toch uitzaaiingen hebben en een volgend moment denk je dan weer, stel je niet aan, 't zijn gewoon je spieren.</p>\n"]),
 ((datetime.datetime(2007, 1, 29, 4, 0),
   datetime.datetime(2007, 1, 30, 4, 0)),
  [u'<p><span style="color:indigo">omhoog voor ervaringen met het invriezen van eicellen</span></p>\n']),
 ((datetime.datetime(2005, 5, 18, 4, 0),
   datetime.datetime(2005, 5, 19, 4, 0)),
  [u"<p>Hoi Jori,</p>\n<p>Ik gebruik zoladex en arimidex, en heb ook last van gewrichtspijn. Het begon met tintelende h

In [141]:
# connect posts to times, per user
for user in T:
    print user
    for t in T[user]:
        # check of t binnen de huidige bin valt. zo ja: voeg toe. zo nee: maak nieuwe bin en voeg daaraan toe. 
        # (posts worden chronologisch opgehaald, van vroeger naar heden)
        print t
        print P[user][T[user].index(t)]

1322
20/01/2007 - 08:33
<p>
</p><div class="bb-quote"><b>twin schreef:</b><br /><blockquote class="bb-quote-body">Ik heb het over botontkalking met mijn huisarts gehad en hij zei dat ik wat extra melk producten moets nemen.<br />
Dat ik daar verder niets voor hoefde nemen.<br />
En dat hij over een poosje een botdichtheidsmeting ging regelen...</blockquote>
</div>

<p>Ik heb me suf zitten peinzen waar ik de artikelen (oa van de WHO) kon vinden, niet gelukt (sorry)  :oops: , maar toch maar even zeggen (zonder verwijzingen en links dan nog): uit onderzoek blijkt dat de calcium in melk(producten) de calcium is die het slechtst opgenomen wordt in het lichaam... Het feit dat je melk(producten) moet drinken om botontkalking te voorkomen is achterhaald en het verbaast me dat een arts dat nog adviseert. In bv de Verenigde Staten, waar de meeste zuivel geconsumeerd wordt per hoofd van de bevolking is ook het aantal mensen dat last krijgt van botontkalking het grootst, relatief gezien (!). Calci